# Quantum Processes and Computation (with PyZX!): Part 2

_Aleks Kissinger | 2020_

Welcome to the second in a series of practicals which will build up from basics to using the ZX calculus to do some interesting and potentially useful stuff on a real quantum computer.

These practicals are designed to go with the [Quantum Processes and Computation](https://www.cs.ox.ac.uk/teaching/courses/2020-2021/quantum/) course taught in Oxford, but if you came across these another way, or just happened up them, you are more than welcome to give them a go! In part 1, we saw how to:
1. construct quantum circuits and ZX-diagrams programmatically
2. evaluate/simulate them numerically
3. do basic diagrammatic reasoning with software

In this part, we will use some of the techniques from part 1 to do _automated_ diagrammatic reasoning and circuit optimisation with the ZX-calculus. We will also be translating the circuits that come out into a format that is useable by IBM's [qiskit](https://qiskit.org/) library, and running those circuits on a real quantum computer!

_These practicals, like PyZX itself are released under the [Apache 2](https://github.com/Quantomatic/pyzx/blob/master/LICENSE) open-source license. Feel free to use, copy, and modify them at will, e.g. to use your own course._

In [ ]:
%pip install pyzx

In [ ]:
import sys, os, math, random
from fractions import Fraction
sys.path.insert(0,os.path.expanduser('~/git/pyzx')) # git version

import pyzx as zx
from pyzx import print_matrix
from pyzx.basicrules import *

from qiskit.test.mock import FakeAthens
from qiskit import QuantumCircuit, Aer, IBMQ, execute
from qiskit.compiler import assemble
from qiskit.tools.monitor import job_monitor
import matplotlib.pyplot as plt

In [ ]:
Z = zx.VertexType.Z
X = zx.VertexType.X
B = zx.VertexType.BOUNDARY
SE = zx.EdgeType.SIMPLE
HE = zx.EdgeType.HADAMARD

In the next few questions, we will use to rules from part 1 to do automatic optimisation of quantum circuits. To provide a baseline for comparison, we will start by writing a naive circuit optimiser, which performs basic gate cancellations.

Here's a bit of a template with some comments to get us started:

In [ ]:
def circuit_optimizer(circ):
    c = circ.copy()
    
    # keep looping until we return a circuit
    while True:
        new_gates = []
        
        # search through the gates in circuit c in order
        for g in c.gates:
            
            # if current and last gate are both Z-phase gates...
            if (len(new_gates) > 0 and
                  isinstance(new_gates[-1], zx.gates.ZPhase) and
                  isinstance(g, zx.gates.ZPhase) and
                  new_gates[-1].target == g.target):
                
                # ...combine the phases into a single phase gate
                g1 = zx.gates.ZPhase(g.target, new_gates[-1].phase + g.phase)
                new_gates[-1] = g1
            
            # otherwise just save the current gate
            else:
                new_gates.append(g)
        
        # if we actually got a smaller circuit...
        if len(new_gates) < len(c.gates):
            c.gates = new_gates # ...save it and continue
        else:
            return c # ...otherwise return the circuit

This code will combine the phases in adjacent `ZPhase` gates (i.e. gates produced by `s`, `t` or `rz(.)` in QASM).

Lets see it in action:

In [ ]:
demo_circ = zx.qasm("""
qreg q[3];

t q[0];
t q[0];
t q[0];
cx q[0], q[1];
cx q[1], q[2];
cx q[1], q[2];
cx q[0], q[1];
t q[2];
""")
demo_opt = circuit_optimizer(demo_circ)

print("original:")
zx.draw(demo_circ)
print("optimised:")
zx.draw(demo_opt)

This works okay, but it could be much better.

<hr style="border-bottom:3px solid black" />

## Question 2.1

Make a new function `circuit_optimizer2` that improves on the one above by:
 1. cancelling adjacent pairs of CNOT and Hadamard gates
 2. adding together the phases in adjacent `XPhase` gates (`rx(.)` gates in QASM)
 3. removing X or Z phase gates with a phase of `0`

Apply your function to a test circuit and check that it preserves the overall unitary using `zx.compare_tensors`.

<i><b>Note:</b> By "adjacent gates", we mean gates that are next to each other in the `gates` list with the same `target` property (in the case of Hadamard gates) and the same `control` and `target` properties (for CNOT gates) .</i>


<hr style="border-bottom:3px solid black" />

<hr style="border-bottom:3px solid black" />

## Question 2.2

Use `zx.generate.CNOT_HAD_PHASE_circuit` (see [Documentation](https://pyzx.readthedocs.io/en/latest/api.html#generating-circuits)) to generate 100 random circuits with 4, 5, and 6 qubits and gate depth 20. Test your `circuit_optimizer2` function is producing the correct output circuit for each using `zx.compare_tensors`.

<hr style="border-bottom:3px solid black" />

Now we'll adopt an alternative approach, based on doing ZX-calculus simplifications. First we'll implement a simplifier using some of the techniques we learning in part 1.

<hr style="border-bottom:3px solid black" />

## Question 2.3

Implement a function called `zx_simplify` that performs spider fusion and removes identities as much as possible on a ZX-diagram. Test your simplifier on random circuits using `zx.tensor_compare` as in question 2.2.

<hr style="border-bottom:3px solid black" />

Now comes the tricky part! If we start with a circuit, we can call `c.to_graph()` to get a ZX-diagram, and do all sorts of simplifications using the rules of the ZX-calculus. But how do we get a circuit back out?

In the general case, this is still an open problem! Solving it in special cases has been the subject of two recent papers:
 * [Graph-theoretic Simplification of Quantum Circuits with the ZX-calculus](https://arxiv.org/abs/1902.03178)
 * [There and back again: A circuit extraction tale](https://arxiv.org/abs/2003.01664)

In our case, we started with a circuit and only applied spider-fusion and identity-removal laws. This makes circuit extraction relatively simple: we just need to "unfuse" some spiders again to get gates back out.

Written more algorithmically, we can do the following. Start with a graph and an empty circuit `circ`, and pull spiders and edges out of the graph and turn them into gates in `circ`. That is:
 1. If any of outputs of the graph are connected to Hadamard edges, prepend a Hadamard gate to `circ` and change to normal edges.
 2. If any vertices adjacent to an output are Z or X vertices with degree 2, prepend the appropriate kind of phase gate to `circ`, remove the vertex from the graph, and go to step 1. Otherwise continue.
 3. If any pairs of vertices are both adjacent to outputs and are connected by an edge, delete that edge and prepend the appropriate kind of 2-qubit gate to `circ`. For example, if vertex 1 is a Z vertex and vertex 2 is an X vertex, prepend a CNOT gate to `circ`. If we removed an edge, go back to step 2. Otherwise continue.
 4. If we have managed to remove all Z and X nodes in the previous steps, we will be left just with wires. The only thing left to do is insert SWAP gates at the beginning of the circuit to account for any crossing wires in the graph. If we did NOT remove all of the Z or X spiders, the extraction fails.

PyZX has a function for this called `zx.extract_simple`.

<hr style="border-bottom:3px solid black" />

## Question 2.4

Implement a function called `zx_circuit_optimizer` that first simplifies the ZX-diagram of a circuit using `zx_simplify` then extracts the result. Test your optimizer on random circuits using `zx.compare_tensors` as in question 2.2.

<hr style="border-bottom:3px solid black" />

<hr style="border-bottom:3px solid black" />

## Question 2.5

Benchmark the performance of `circuit_optimizer2` and `zx_circuit_optimizer`. That is, provide statistics for how well the optimizer performs at (1) reducing the total gate count and (2) reducing the 2-qubit gate count, for random circuits of various sizes.

There is no "right or wrong" answer to this question, but your results should be informative and you should briefly describe your methodology. For useful methods to analyse circuits, you may wish to have a look at the [documentation](https://pyzx.readthedocs.io/en/latest/api.html).

<hr style="border-bottom:3px solid black" />

## Running on a real quantum computer

Now things are about to get real. We're going to run our circuits on real hardware using the IBM Quantum Experience.

We'll first perform a bit of setup. If you are already running this in the IBM Quantum Experience, the following code will probably just work. If you are running this notebook locally, you will need to set up an IBMid and run a tiny bit of Python code to save your credentials on your computer. Instructions are [here](https://github.com/Qiskit/qiskit-ibmq-provider/#updating-your-ibm-q-experience-credentials). You only need to call `IBMQ.save_account('XXXXXX')` once per computer, then you can delete this from your Jupyter notebook (I don't need to see your personal API key :) ).

In [ ]:
simulator = Aer.get_backend("qasm_simulator")
noisy_simulator = FakeAthens()
try:
    IBMQ.load_account()
    provider = IBMQ.get_provider(hub="ibm-q", group="open", project="main")
    backend = provider.get_backend("ibmq_athens")
except:
    print("Error:", sys.exc_info()[1])
    print("Setting backend to qasm_simulator")
    backend = noisy_simulator

As always, it takes a bit of effort to get different systems to talk to each other. In our case, we need a function for translating PyZX-flavoured circuits in IBM-flavoured (qiskit) circuits. Luckily, these contain pretty much the same data, so the translation is straightforward.

In [ ]:
def pyzx_to_qiskit(circ):
    # converts all gates to CNOT, CZ, HAD, ZPhase, and XPhase
    circ = circ.to_basic_gates()
    q = circ.qubits
    ibm_circ = QuantumCircuit(q, q)
    for g in circ.gates:
        if isinstance(g, zx.gates.CNOT): ibm_circ.cnot(g.control, g.target)
        elif isinstance(g, zx.gates.CZ): ibm_circ.cz(g.control, g.target)
        elif isinstance(g, zx.gates.HAD): ibm_circ.h(g.target)
        elif isinstance(g, zx.gates.ZPhase): ibm_circ.rz(math.pi * g.phase, g.target)
        elif isinstance(g, zx.gates.XPhase): ibm_circ.rx(math.pi * g.phase, g.target)
    
    # measure everything
    ibm_circ.measure(range(q), range(q))
    return ibm_circ

In [ ]:
zx.draw(demo_circ)
ibm_circ = pyzx_to_qiskit(demo_circ)
display(ibm_circ.draw())

`execute` is a function that takes 2 arguments: an IBM-flavoured circuit and a `backend` (e.g. a simulator or a real computer), and returns a `job` object which contains the status (and eventually the results) of a computation. See the [qiskit docs](https://qiskit.org/documentation/apidoc/execute.html) for an example of executing a circuit with the simulator. For the simulator, a job involving a small circuit should be done pretty much instantly.

Once a job is done, you can get the raw data out with `job.result().get_counts()`. Your circuit is run many times (these are called `shots`). `get_counts()` simply tells you how many times each measurement result was observed.

<hr style="border-bottom:3px solid black" />

## Question 2.6

Build a circuit using `zx.qasm`, convert it to qiskit format, and run it using the `simulator` backend. Use the result of `get_counts()` to compute the probability of each outcome, and compare to the probabilities computed in PyZX (as in Question 1.6 of Part 1).

<hr style="border-bottom:3px solid black" />

Like in the old days of classical computers, you'll need to wait in line if you want to run something on a quantum computer. You can see if a job is done by running `job_monitor(job)`. I suggest you do something else while you wait. :)

<hr style="border-bottom:3px solid black" />

## Question 2.7

Build a circuit using `zx.qasm`, convert it to qiskit format, and run it using a real quantum computer as the backend. Again, use the result of `get_counts()` to compute the probability of each outcome, and compare to the probabilities computed in PyZX (as in Question 1.6 of Part 1).

<i>Note: You should call the `decompose()` method of the qiskit circuit to make sure the circuit consists only of gates supported by the hardware. Also, 2-qubit gates can only appear between qubits that are physically connected. Choose your quantum computer and view its connectivity using the "Dashboard" on IBM Quantum Experience. Pay attention to how many jobs are queued, since this indicates how long you'll need to wait.</i>

<p style="color:blue">Although it is obviously more fun to run things on a real quantum computer, if you can't get it to work, you can use <code style="color:blue">noisy_simulator</code> as the backend for this question and the next one. It should have (approximately) the same behaviour as the "ibmq_athens" device.</p>

<hr style="border-bottom:3px solid black" />

<hr style="border-bottom:3px solid black" />

## Question 2.8

Optimise your circuit using one or more of the methods from before and try running it on the hardware again. Do your results improve?

<hr style="border-bottom:3px solid black" />